In [7]:
# -*- coding: utf-8 -*-
import dataiku
import pandas as pd, numpy as np
from dataiku import pandasutils as pdu

from plotly.offline import init_notebook_mode,iplot
import plotly.graph_objects as go
init_notebook_mode(connected=True)


# Read recipe inputs
customer_Analysis = dataiku.Dataset("Customer_Analysis")
customer_Analysis_df = customer_Analysis.get_dataframe()
# df = customer_Analysis.get_dataframe()


# Compute recipe outputs from inputs
# TODO: Replace this part by your actual code that computes the output, as a Pandas dataframe
# NB: DSS also supports other kinds of APIs for reading and writing data. Please see doc.

df = customer_Analysis_df # For this sample code, simply copy input to output

# # Write recipe outputs
# ca_Python = dataiku.Dataset("CA_Python")
# ca_Python.write_with_schema(ca_Python_df)

# EDA (Exploratory Data Analysis)

In [8]:
df.describe()

Customer Lifetime Value        Income  Monthly Premium Auto  Months Since Last Claim  Months Since Policy Inception  Number of Open Complaints  Number of Policies  Total Claim Amount
count              9134.000000   9134.000000           9134.000000              9134.000000                    9134.000000                9134.000000         9134.000000         9134.000000
mean               8004.940475  37657.380009             93.219291                15.097000                      48.064594                   0.384388            2.966170          434.088794
std                6870.967608  30379.904734             34.407967                10.073257                      27.905991                   0.910384            2.390182          290.500092
min                1898.007675      0.000000             61.000000                 0.000000                       0.000000                   0.000000            1.000000            0.099007
25%                3994.251794      0.000000             68.000000                 6.000000                      24.000000                   0.000000            1.000000          272.258244
50%                5780.182197  33889.500000             83.000000                14.000000                      48.000000                   0.000000            2.000000          383.945434
75%                8962.167041  62320.000000            109.000000                23.000000                      71.000000                   0.000000            4.000000          547.514839
max               83325.381190  99981.000000            298.000000                35.000000                      99.000000                   5.000000            9.000000         2893.239678

In [9]:
lab = df["Response"].value_counts().keys().tolist() #Labels
val = df["Response"].value_counts().values.tolist() #Values
trace = go.Pie(labels=lab,
                values=val,
                marker=dict(colors=['blue']),
                hoverinfo="value")

layout = go.Layout(title="Response Distribution")

fig = go.Figure(data = trace,layout = layout)

iplot(fig)

In [10]:
import plotly.express as px

fig = px.histogram(df, x="Sales Channel", color='Response')
fig.show()

In [11]:
fig = px.histogram(df, x="Renew Offer Type", color='Response')
fig.show()

In [12]:
fig = px.histogram(df, x="Education", color='Response')
fig.show()

In [13]:
fig = px.histogram(df, x="EmploymentStatus", color='Response')
fig.show()

In [14]:
fig = px.histogram(df, x="Vehicle Class", color='Response')
fig.show()

In [15]:
fig = px.histogram(df, x="Policy", color='Response')
fig.show()

In [16]:
fig = px.violin(df, y="Total Claim Amount", x="Response",
                box=True, points="all", # hover_data=df.columns,
                title = 'Response Rate by Total Claim Amount')
fig.show()

In [17]:
fig = px.violin(df, y="Income", x="Response",
                box=True, points="all", # hover_data=df.columns,
                title = 'Response Rate by Income')
fig.show()

In [18]:
fig = px.scatter_3d(df, x="Income", y="Monthly Premium Auto",
                    z="Customer Lifetime Value",
                    color="Response", size="Income",
                    color_discrete_map = {"Income": "blue",
                                          "Monthly Premium Auto": "green",
                                          "Customer Lifetime Value":"red"})
fig.show()

# Regression Analysis with Continuous Variables

In [19]:
# make response a numerical value
df.Response = df.Response.apply(lambda X : 0 if X == 'No' else 1)

In [20]:
import statsmodels.api as sm # ok

In [21]:
cont_df = df.select_dtypes(include=['int64','float'])

In [22]:
cont_df.nunique()

Customer Lifetime Value          8041
Response                            2
Income                           5694
Monthly Premium Auto              202
Months Since Last Claim            36
Months Since Policy Inception     100
Number of Open Complaints           6
Number of Policies                  9
Total Claim Amount               5106
dtype: int64

In [23]:
cont_reg = sm.Logit(cont_df['Response'],
                             cont_df.drop('Response', axis = 1))
cont_reg.fit().summary()

Optimization terminated successfully.
         Current function value: 0.421189
         Iterations 6


<class 'statsmodels.iolib.summary.Summary'>
"""
                           Logit Regression Results                           
==============================================================================
Dep. Variable:               Response   No. Observations:                 9134
Model:                          Logit   Df Residuals:                     9126
Method:                           MLE   Df Model:                            7
Date:                Mon, 29 Jun 2020   Pseudo R-squ.:                -0.02546
Time:                        13:37:31   Log-Likelihood:                -3847.1
converged:                       True   LL-Null:                       -3751.6
                                        LLR p-value:                     1.000
=================================================================================================
                                    coef    std err          z      P>|z|      [0.025      0.975]
-------------------------------------------------------------------------------------------------
Customer Lifetime Value       -6.741e-06   5.04e-06     -1.337      0.181   -1.66e-05    3.14e-06
Income                        -2.857e-06   1.03e-06     -2.766      0.006   -4.88e-06   -8.33e-07
Monthly Premium Auto             -0.0084      0.001     -6.889      0.000      -0.011      -0.006
Months Since Last Claim          -0.0202      0.003     -7.238      0.000      -0.026      -0.015
Months Since Policy Inception    -0.0060      0.001     -6.148      0.000      -0.008      -0.004
Number of Open Complaints        -0.0829      0.034     -2.424      0.015      -0.150      -0.016
Number of Policies               -0.0810      0.013     -6.356      0.000      -0.106      -0.056
Total Claim Amount                0.0001      0.000      0.711      0.477      -0.000       0.000
=================================================================================================
"""

In [24]:
import matplotlib.pyplot as plt
import seaborn as sns

plt.figure(figsize=(10,6))
sns.heatmap(cont_df.corr(), annot = True)
plt.show()

# Regression Analysis with Categorical Variables

In [25]:
categorical_df = df.select_dtypes(include='object')
cat_df = categorical_df.drop(['Customer','Effective To Date'], axis = 1)

In [26]:
cat_df.nunique()

State               5
Coverage            3
Education           5
EmploymentStatus    5
Gender              2
Location Code       3
Marital Status      3
Policy Type         3
Policy              9
Renew Offer Type    4
Sales Channel       4
Vehicle Class       6
Vehicle Size        3
dtype: int64

In [27]:
cols=cat_df.columns.tolist()

In [28]:
from sklearn.preprocessing import LabelEncoder
lb = LabelEncoder()
for col in cat_df[cols]:
    cat_df[col] = lb.fit_transform(cat_df[col])

In [29]:
from sklearn.preprocessing import LabelEncoder
for col in cat_df[cols]:
    cat_df[col] = LabelEncoder().fit_transform(cat_df[col])

In [30]:
cat_df.head()

State  Coverage  Education  EmploymentStatus  Gender  Location Code  Marital Status  Policy Type  Policy  Renew Offer Type  Sales Channel  Vehicle Class  Vehicle Size
0      4         0          0                 1       0              1               1            0       2                 0              0              5             1
1      0         1          0                 4       0              1               2            1       5                 2              0              0             1
2      2         2          0                 1       0              1               1            1       5                 0              0              5             1
3      1         0          0                 4       1              1               1            0       1                 0              2              3             1
4      4         0          0                 1       1              0               2            1       3                 0              0              0             1

In [31]:
categorical_train = sm.Logit(cont_df.Response, cat_df)
categorical_train.fit().summary()

Optimization terminated successfully.
         Current function value: 0.387557
         Iterations 7


<class 'statsmodels.iolib.summary.Summary'>
"""
                           Logit Regression Results                           
==============================================================================
Dep. Variable:               Response   No. Observations:                 9134
Model:                          Logit   Df Residuals:                     9121
Method:                           MLE   Df Model:                           12
Date:                Mon, 29 Jun 2020   Pseudo R-squ.:                 0.05642
Time:                        13:37:32   Log-Likelihood:                -3539.9
converged:                       True   LL-Null:                       -3751.6
                                        LLR p-value:                 4.224e-83
====================================================================================
                       coef    std err          z      P>|z|      [0.025      0.975]
------------------------------------------------------------------------------------
State               -0.0256      0.023     -1.122      0.262      -0.070       0.019
Coverage            -0.0639      0.046     -1.390      0.164      -0.154       0.026
Education            0.0088      0.022      0.409      0.683      -0.033       0.051
EmploymentStatus    -0.0459      0.024     -1.951      0.051      -0.092       0.000
Gender               0.0466      0.060      0.774      0.439      -0.071       0.165
Location Code       -0.0477      0.047     -1.014      0.311      -0.140       0.045
Marital Status      -0.4643      0.047     -9.816      0.000      -0.557      -0.372
Policy Type          0.1736      0.132      1.311      0.190      -0.086       0.433
Policy              -0.0751      0.037     -2.033      0.042      -0.147      -0.003
Renew Offer Type    -0.5681      0.037    -15.226      0.000      -0.641      -0.495
Sales Channel       -0.2150      0.030     -7.148      0.000      -0.274      -0.156
Vehicle Class        0.0201      0.015      1.381      0.167      -0.008       0.049
Vehicle Size        -0.3355      0.052     -6.398      0.000      -0.438      -0.233
====================================================================================
"""

# Regression Analysis with both Continuous and Categorical Variables

In [32]:
cont_df.reset_index(drop = True, inplace=True)
cat_df.reset_index(drop = True, inplace=True)

In [33]:
combined_df = pd.concat([cont_df,cat_df], axis = 1)

In [34]:
combined_df.head()

Customer Lifetime Value  Response  Income  Monthly Premium Auto  Months Since Last Claim  Months Since Policy Inception  Number of Open Complaints  Number of Policies  Total Claim Amount  State  Coverage  Education  EmploymentStatus  Gender  Location Code  Marital Status  Policy Type  Policy  Renew Offer Type  Sales Channel  Vehicle Class  Vehicle Size
0              2763.519279         0   56274                    69                       32                              5                          0                   1          384.811147      4         0          0                 1       0              1               1            0       2                 0              0              5             1
1              6979.535903         0       0                    94                       13                             42                          0                   8         1131.464935      0         1          0                 4       0              1               2            1       5                 2              0              0             1
2             12887.431650         0   48767                   108                       18                             38                          0                   2          566.472247      2         2          0                 1       0              1               1            1       5                 0              0              5             1
3              7645.861827         0       0                   106                       18                             65                          0                   7          529.881344      1         0          0                 4       1              1               1            0       1                 0              2              3             1
4              2813.692575         0   43836                    73                       12                             44                          0                   1          138.130879      4         0          0                 1       1              0               2            1       3                 0              0              0             1

In [35]:
combined_train = sm.Logit(combined_df.Response, combined_df.drop(['Response'], axis = 1))
combined_train.fit().summary()

Optimization terminated successfully.
         Current function value: 0.384709
         Iterations 7


<class 'statsmodels.iolib.summary.Summary'>
"""
                           Logit Regression Results                           
==============================================================================
Dep. Variable:               Response   No. Observations:                 9134
Model:                          Logit   Df Residuals:                     9113
Method:                           MLE   Df Model:                           20
Date:                Mon, 29 Jun 2020   Pseudo R-squ.:                 0.06336
Time:                        13:37:32   Log-Likelihood:                -3513.9
converged:                       True   LL-Null:                       -3751.6
                                        LLR p-value:                 4.066e-88
=================================================================================================
                                    coef    std err          z      P>|z|      [0.025      0.975]
-------------------------------------------------------------------------------------------------
Customer Lifetime Value       -1.183e-05   5.11e-06     -2.317      0.021   -2.18e-05   -1.82e-06
Income                         3.347e-06   1.39e-06      2.411      0.016    6.26e-07    6.07e-06
Monthly Premium Auto             -0.0033      0.001     -2.471      0.013      -0.006      -0.001
Months Since Last Claim          -0.0053      0.003     -1.780      0.075      -0.011       0.001
Months Since Policy Inception    -0.0019      0.001     -1.830      0.067      -0.004       0.000
Number of Open Complaints        -0.0569      0.035     -1.622      0.105      -0.126       0.012
Number of Policies               -0.0392      0.013     -3.013      0.003      -0.065      -0.014
Total Claim Amount                0.0007      0.000      4.448      0.000       0.000       0.001
State                            -0.0084      0.023     -0.357      0.721      -0.054       0.038
Coverage                         -0.0325      0.053     -0.615      0.538      -0.136       0.071
Education                         0.0235      0.022      1.068      0.285      -0.020       0.067
EmploymentStatus                 -0.0232      0.030     -0.763      0.445      -0.083       0.036
Gender                            0.0584      0.061      0.950      0.342      -0.062       0.179
Location Code                    -0.0894      0.053     -1.696      0.090      -0.193       0.014
Marital Status                   -0.4645      0.048     -9.585      0.000      -0.559      -0.370
Policy Type                       0.1085      0.135      0.806      0.420      -0.155       0.372
Policy                           -0.0335      0.039     -0.864      0.388      -0.110       0.043
Renew Offer Type                 -0.5828      0.039    -15.136      0.000      -0.658      -0.507
Sales Channel                    -0.1937      0.030     -6.354      0.000      -0.253      -0.134
Vehicle Class                     0.0287      0.015      1.897      0.058      -0.001       0.058
Vehicle Size                     -0.2837      0.055     -5.161      0.000      -0.391      -0.176
=================================================================================================
"""

# Regression Analysis with excluding Non-significant variables

In [36]:
significant_cols = ['Customer Lifetime Value','Income','Monthly Premium Auto','Months Since Last Claim',
                    'Months Since Policy Inception','Number of Policies','Total Claim Amount','Marital Status',
                    'Renew Offer Type','Sales Channel','Vehicle Size']
trainData = sm.Logit(combined_df.Response, combined_df[significant_cols])
trainData.fit().summary()

Optimization terminated successfully.
         Current function value: 0.385476
         Iterations 7


<class 'statsmodels.iolib.summary.Summary'>
"""
                           Logit Regression Results                           
==============================================================================
Dep. Variable:               Response   No. Observations:                 9134
Model:                          Logit   Df Residuals:                     9123
Method:                           MLE   Df Model:                           10
Date:                Mon, 29 Jun 2020   Pseudo R-squ.:                 0.06149
Time:                        13:37:32   Log-Likelihood:                -3520.9
converged:                       True   LL-Null:                       -3751.6
                                        LLR p-value:                 7.814e-93
=================================================================================================
                                    coef    std err          z      P>|z|      [0.025      0.975]
-------------------------------------------------------------------------------------------------
Customer Lifetime Value       -1.129e-05   5.09e-06     -2.217      0.027   -2.13e-05   -1.31e-06
Income                         3.549e-06   1.11e-06      3.192      0.001    1.37e-06    5.73e-06
Monthly Premium Auto             -0.0033      0.001     -2.762      0.006      -0.006      -0.001
Months Since Last Claim          -0.0062      0.003     -2.102      0.036      -0.012      -0.000
Months Since Policy Inception    -0.0023      0.001     -2.238      0.025      -0.004      -0.000
Number of Policies               -0.0414      0.013     -3.226      0.001      -0.067      -0.016
Total Claim Amount                0.0006      0.000      4.148      0.000       0.000       0.001
Marital Status                   -0.4794      0.045    -10.664      0.000      -0.567      -0.391
Renew Offer Type                 -0.5793      0.038    -15.268      0.000      -0.654      -0.505
Sales Channel                    -0.1981      0.030     -6.539      0.000      -0.257      -0.139
Vehicle Size                     -0.3031      0.053     -5.690      0.000      -0.407      -0.199
=================================================================================================
"""

# Classification

In [37]:
y = combined_df.Response
X = combined_df.drop('Response', axis = 1)

In [38]:
from sklearn.model_selection import train_test_split, cross_validate

X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size = 0.2, random_state = 42)

# SVC Classification

In [39]:
from sklearn.metrics import confusion_matrix, accuracy_score, classification_report
from sklearn.svm import SVC

svc = SVC(gamma='auto')
svc.fit(X_train, y_train)
svc_pred = svc.predict(X_test)

print(confusion_matrix(svc_pred,y_test))
print('Accuracy_score:',accuracy_score(svc_pred, y_test))
print(classification_report(svc_pred, y_test))

cross_val_score_svc = cross_validate(svc, X_train, y_train,cv = 5,return_train_score=True)
print('Cross validation Train_score',cross_val_score_svc['train_score'].mean())
print('Cross validation Test_score',cross_val_score_svc['test_score'].mean())

[[1561   18]
 [   0  248]]
('Accuracy_score:', 0.9901477832512315)
              precision    recall  f1-score   support

           0       1.00      0.99      0.99      1579
           1       0.93      1.00      0.96       248

   micro avg       0.99      0.99      0.99      1827
   macro avg       0.97      0.99      0.98      1827
weighted avg       0.99      0.99      0.99      1827

('Cross validation Train_score', 1.0)
('Cross validation Test_score', 0.9849456596544354)


# Random Forest Classification

In [40]:
from sklearn.ensemble import RandomForestClassifier
rfc = RandomForestClassifier(n_estimators=100)
rfc.fit(X_train, y_train)
rfc_pred = rfc.predict(X_test)

print(confusion_matrix(rfc_pred,y_test))
print('Accuracy score:',accuracy_score(rfc_pred, y_test))
print(classification_report(rfc_pred, y_test))

cross_val_score_rfc = cross_validate(rfc, X_train, y_train,cv = 5,return_train_score=True)

print('Cross validation train_score',cross_val_score_rfc['train_score'].mean())
print('Cross validation test_score',cross_val_score_rfc['test_score'].mean())

[[1558    1]
 [   3  265]]
('Accuracy score:', 0.9978106185002736)
              precision    recall  f1-score   support

           0       1.00      1.00      1.00      1559
           1       1.00      0.99      0.99       268

   micro avg       1.00      1.00      1.00      1827
   macro avg       1.00      0.99      1.00      1827
weighted avg       1.00      1.00      1.00      1827

('Cross validation train_score', 1.0)
('Cross validation test_score', 0.9939783200420228)


# Feature Importance

In [41]:
feature_imp = rfc.feature_importances_.round(3)
ser_rank = pd.Series(feature_imp,
                     index=X.columns).sort_values(ascending = False)

plt.figure(figsize=(12,7))
sns.barplot(x= ser_rank.values, y = ser_rank.index, palette='deep')
plt.xlabel('relative importance')
plt.show()